Jack Dennison

Question 1

In [32]:
import pandas as pd

csv = '/Users/jackdennison/Downloads/rodent_2022-2023.csv'
df = pd.read_csv(csv)
df.to_sql("rodents", con=sqlite3.connect("rodents.db"), if_exists="replace")


82869

Question 2

In [33]:
import sqlite3
import csv

# Connect to the SQLite database
conn = sqlite3.connect('agency.db')
cursor = conn.cursor()

# Create the agency table
cursor.execute('''
    CREATE TABLE IF NOT EXISTS agency (
        id INTEGER PRIMARY KEY,
        agency TEXT,
        agency_name TEXT
    )
''')

# Commit the changes before accessing the CSV file
conn.commit()

# Open the CSV file and insert data into the agency table
with open('/Users/jackdennison/Downloads/rodent_2022-2023.csv', 'r', encoding='utf-8-sig') as file:
    reader = csv.DictReader(file)
    for row in reader:
        cursor.execute('''
            INSERT INTO agency (agency, agency_name) VALUES (?, ?)
        ''', (row['Agency'], row['Agency Name']))

# Commit the changes after inserting data
conn.commit()

# Close the connection
conn.close()

Question 3: The agency name was already removed from the csv file as part of the Rodent Data Cleaning Assignment as a redundant column. The reason that it is redundant is that the only difference between the two columns is the "Agency" column abbreviates the name (DOHMH) while the "Agency Name" column lists the full name (Department of Health and Mental Hygiene)

Question 4

In [34]:
import sqlite3
import csv
import pandas as pd

# Create a new SQLite database connection
conn = sqlite3.connect('rodents2.db')
cursor = conn.cursor()

# Create the rodent2 table
cursor.execute('''
    CREATE TABLE IF NOT EXISTS rodent2 (
        Unique_Key TEXT PRIMARY KEY,
        Created_Date TEXT,
        Closed_Date TEXT,
        Agency TEXT,
        Agency_Name TEXT,
        Complaint_Type TEXT,
        Descriptor TEXT,
        Location_Type TEXT,
        Incident_Zip TEXT,
        Incident_Address TEXT,
        Cross_Street_1 TEXT,
        Cross_Street_2 TEXT,
        Status TEXT,
        Resolution_Description TEXT,
        Community_Board TEXT,
        BBL TEXT,
        Borough TEXT,
        X_Coordinate_State_Plane TEXT,
        Y_Coordinate_State_Plane TEXT,
        Open_Data_Channel_Type TEXT,
        Latitude TEXT,
        Longitude TEXT,
        Location TEXT,
        Community_Districts TEXT,
        Borough_Boundaries TEXT,
        City_Council_Districts TEXT,
        Police_Precincts TEXT
    )
''')

# Import data from CSV to rodent2 table, handling duplicates
with open('/Users/jackdennison/Downloads/rodent_2022-2023.csv', 'r', encoding='utf-8-sig') as file:
    reader = csv.DictReader(file)
    for row in reader:
        try:
            cursor.execute('''
                INSERT INTO rodent2 (
                    Unique_Key, Created_Date, Closed_Date, Agency, Agency_Name, Complaint_Type,
                    Descriptor, Location_Type, Incident_Zip, Incident_Address,
                    Cross_Street_1, Cross_Street_2, Status, Resolution_Description,
                    Community_Board, BBL, Borough, X_Coordinate_State_Plane,
                    Y_Coordinate_State_Plane, Open_Data_Channel_Type, Latitude,
                    Longitude, Location, Community_Districts, Borough_Boundaries,
                    City_Council_Districts, Police_Precincts
                ) VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
            ''', (
                row['Unique Key'], row['Created Date'], row['Closed Date'], row['Agency'], row['Agency Name'],
                row['Complaint Type'], row['Descriptor'], row['Location Type'], row['Incident Zip'],
                row['Incident Address'], row['Cross Street 1'], row['Cross Street 2'], row['Status'],
                row['Resolution Description'], row['Community Board'], row['BBL'], row['Borough'],
                row['X Coordinate (State Plane)'], row['Y Coordinate (State Plane)'],
                row['Open Data Channel Type'], row['Latitude'], row['Longitude'], row['Location'],
                row['Community Districts'], row['Borough Boundaries'], row['City Council Districts'],
                row['Police Precincts']
            ))
        except sqlite3.IntegrityError as e:
            print(f"Skipping duplicate row: {e}")
            # You can choose to skip the duplicate row or update the existing row here

# Commit changes to the database
conn.commit()


# Close the cursor and connection
cursor.close()
conn.close()

# Read data from the database into a DataFrame
conn = sqlite3.connect('rodents2.db')
df = pd.read_sql_query('SELECT * FROM rodent2', conn)
print(df.head())

# Close the connection
conn.close()


Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE constraint failed: rodent2.Unique_Key
Skipping duplicate row: UNIQUE con

In [35]:
import sqlite3

# Connect to the SQLite database
conn = sqlite3.connect('rodents2.db')
cursor = conn.cursor()

# Count the number of rows in the rodent2 table
cursor.execute('SELECT COUNT(*) FROM rodent2')
count_rodent2 = cursor.fetchone()[0]

# Connect to the SQLite database containing the original rodent table
conn_original = sqlite3.connect('rodents.db')
cursor_original = conn_original.cursor()

# Count the number of rows in the original rodent table
cursor_original.execute('SELECT COUNT(*) FROM rodents')
count_rodent = cursor_original.fetchone()[0]

# Print the sizes of both tables
print("Size of rodent2 table:", count_rodent2)
print("Size of rodent table:", count_rodent)

# Close the connections
conn.close()
conn_original.close()


Size of rodent2 table: 82869
Size of rodent table: 82869


From this analysis, it appears that the two tables are the same size, which is interesting.

In [39]:
import sqlite3

# Connect to the SQLite database
conn = sqlite3.connect('rodents.db')
cursor = conn.cursor()

# Identify unique agencies
cursor.execute('SELECT DISTINCT Agency FROM rodents')
unique_agencies = [row[0] for row in cursor.fetchall()]

# Create a dictionary to map agency names to integer codes
agency_to_code = {agency: code for code, agency in enumerate(unique_agencies, start=1)}

# Add the agency_code column to the rodent table
cursor.execute('ALTER TABLE rodents ADD COLUMN agency_code INTEGER')

# Update the rodent table with agency codes
for agency, code in agency_to_code.items():
    cursor.execute('''
        UPDATE rodents
        SET agency_code = ?
        WHERE Agency = ?
    ''', (code, agency))

# Commit the changes to the database
conn.commit()

# Close the connection
conn.close()
